# CMU notebook

Follow the guide and fill in any place that says `YOUR CODE HERE` or "YOUR ANSWER HERE."

#CMU 10605/10805 Machine Learning with Large Datasets

## Homework 1 - Coding 2: ML Pipeline

In [0]:
# YOU CAN MOST LIKELY IGNORE THIS CELL. This is only of use for running this notebook locally.

# THIS CELL DOES NOT NEED TO BE RUN ON DATABRICKS. 
# Note that Databricks already creates a SparkContext for you, so this cell can be skipped.
# This cell should be NOT be commented when submitting to Gradescope
import findspark
findspark.init()
import pyspark
from pyspark.sql import SQLContext
sc = pyspark.SparkContext(appName="hw")
sqlContext = SQLContext(sc)

print("spark context started")

'\nimport findspark\nfindspark.init()\nimport pyspark\nfrom pyspark.sql import SQLContext\nsc = pyspark.SparkContext(appName="hw")\nsqlContext = SQLContext(sc)\n\nprint("spark context started")\n'

# 2. Power Plant Machine Learning Pipeline Application
This section is an end-to-end exercise of performing Extract-Transform-Load and Exploratory Data Analysis on a real-world dataset, and then applying several different machine learning algorithms to solve a supervised regression problem on the dataset.

** This excercise covers: **
* *Part 1: Business Understanding*
* *Part 2: Load Your Data*
* *Part 3: Explore Your Data*
* *Part 4: Visualize Your Data*
* *Part 5: Data Preparation*
* *Part 6: Data Modeling*
* *Part 7: Tuning and Evaluation*

*Our goal is to accurately predict power output given a set of environmental readings from various sensors in a natural gas-fired power generation plant.*

## Part 1: Business Understanding

** Background **

Power generation is a complex process, and understanding and predicting power output is an important element in managing a plant and its connection to the power grid. The operators of a regional power grid create predictions of power demand based on historical information and environmental factors (e.g., temperature). They then compare the predictions against available resources (e.g., coal, natural gas, nuclear, solar, wind, hydro power plants). Power generation technologies such as solar and wind are highly dependent on environmental conditions, and all generation technologies are subject to planned and unplanned maintenance.

Here is an real-world example of predicted demand (on two time scales), actual demand, and available resources from the California power grid: http://www.caiso.com/Pages/TodaysOutlook.aspx

![](http://content.caiso.com/outlook/SP/ems_small.gif)

The challenge for a power grid operator is how to handle a shortfall in available resources versus actual demand. There are three solutions to  a power shortfall: build more base load power plants (this process can take many years to decades of planning and construction), buy and import power from other regional power grids (this choice can be very expensive and is limited by the power transmission interconnects between grids and the excess power available from other grids), or turn on small [Peaker or Peaking Power Plants](https://en.wikipedia.org/wiki/Peaking_power_plant). Because grid operators need to respond quickly to a power shortfall to avoid a power outage, grid operators rely on a combination of the last two choices. In this exercise, we'll focus on the last choice.

** The Business Problem **

Because they supply power only occasionally, the power supplied by a peaker power plant commands a much higher price per kilowatt hour than power from a power grid's base power plants. A peaker plant may operate many hours a day, or it may operate only a few hours per year, depending on the condition of the region's electrical grid. Because of the cost of building an efficient power plant, if a peaker plant is only going to be run for a short or highly variable time it does not make economic sense to make it as efficient as a base load power plant. In addition, the equipment and fuels used in base load plants are often unsuitable for use in peaker plants because the fluctuating conditions would severely strain the equipment.

The power output of a peaker power plant varies depending on environmental conditions, so the business problem is _predicting the power output of a peaker power plant as a function of the environmental conditions_ -- since this would enable the grid operator to make economic tradeoffs about the number of peaker plants to turn on (or whether to buy expensive power from another grid).

Given this business problem, we need to first perform Exploratory Data Analysis to understand the data and then translate the business problem (predicting power output as a function of envionmental conditions) into a Machine Learning task.  In this instance, the ML task is regression since the label (or target) we are trying to predict is numeric. We will use an [Apache Spark ML Pipeline](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark-ml-package) to perform the regression.

The real-world data we are using in this notebook consists of 9,568 data points, each with 4 environmental attributes collected from a Combined Cycle Power Plant over 6 years (2006-2011), and is provided by the University of California, Irvine at [UCI Machine Learning Repository Combined Cycle Power Plant Data Set](https://archive.ics.uci.edu/ml/datasets/Combined+Cycle+Power+Plant). You can find more details about the dataset on the UCI page, including the following background publications:
* Pinar Tüfekci, [Prediction of full load electrical power output of a base load operated combined cycle power plant using machine learning methods](http://www.journals.elsevier.com/international-journal-of-electrical-power-and-energy-systems/), International Journal of Electrical Power & Energy Systems, Volume 60, September 2014, Pages 126-140, ISSN 0142-0615.
* Heysem Kaya, Pinar Tüfekci and Fikret S. Gürgen: [Local and Global Learning Methods for Predicting Power of a Combined Gas & Steam Turbine](http://psrcentre.org/images/extraimages/70.%20312595.pdf), Proceedings of the International Conference on Emerging Trends in Computer and Electronics Engineering ICETCEE 2012, pp. 13-18 (Mar. 2012, Dubai).

**Suggested**: Read the documentation and examples for [Spark Machine Learning Pipeline](https://spark.apache.org/docs/1.6.2/ml-guide.html#main-concepts-in-pipelines).

As described in the overview we are trying to predict power output given a set of readings from various sensors in a gas-fired power generation plant. The problem is a regression problem since the label (or target) we are trying to predict is numeric.

## Part 2: Extract-Transform-Load (ETL) Your Data

Now that we understand what we are trying to do, the first step is to load our data into a format we can query and use.  This is known as ETL or "Extract-Transform-Load".  We will load our file from Amazon S3.

Note: Alternatively we could upload our data using "Databricks Menu > Tables > Create Table", assuming we had the raw files on our local computer.

Our data is available on Amazon s3 at the following path:

```
dbfs:/databricks-datasets/power-plant/data
```

**To Do:** Let's start by printing a sample of the data.

We'll use the built-in Databricks functions for exploring the Databricks filesystem (DBFS)

Use `display(dbutils.fs.ls("/databricks-datasets/power-plant/data"))` to list the files in the directory

In [0]:
# Uncomment the following code to run it in databricks

display(dbutils.fs.ls("/databricks-datasets/power-plant/data"))

path name size modificationTime dbfs:/databricks-datasets/power-plant/data/Sheet1.tsv Sheet1.tsv 308693 1436833478000 dbfs:/databricks-datasets/power-plant/data/Sheet2.tsv Sheet2.tsv 308693 1436833478000 dbfs:/databricks-datasets/power-plant/data/Sheet3.tsv Sheet3.tsv 308693 1436833478000 dbfs:/databricks-datasets/power-plant/data/Sheet4.tsv Sheet4.tsv 308693 1436833478000 dbfs:/databricks-datasets/power-plant/data/Sheet5.tsv Sheet5.tsv 308693 1436833479000

Next, use the `dbutils.fs.head` command to look at the first 65,536 bytes of the first file in the directory.

Use `print dbutils.fs.head("/databricks-datasets/power-plant/data/Sheet1.tsv")` to list the files in the directory

In [0]:
print (dbutils.fs.head("/databricks-datasets/power-plant/data/Sheet1.tsv"))

[Truncated to first 65536 bytes]
AT	V	AP	RH	PE
14.96	41.76	1024.07	73.17	463.26
25.18	62.96	1020.04	59.08	444.37
5.11	39.4	1012.16	92.14	488.56
20.86	57.32	1010.24	76.64	446.48
10.82	37.5	1009.23	96.62	473.9
26.27	59.44	1012.23	58.77	443.67
15.89	43.96	1014.02	75.24	467.35
9.48	44.71	1019.12	66.43	478.42
14.64	45	1021.78	41.25	475.98
11.74	43.56	1015.14	70.72	477.5
17.99	43.72	1008.64	75.04	453.02
20.14	46.93	1014.66	64.22	453.99
24.34	73.5	1011.31	84.15	440.29
25.71	58.59	1012.77	61.83	451.28
26.19	69.34	1009.48	87.59	433.99
21.42	43.79	1015.76	43.08	462.19
18.21	45	1022.86	48.84	467.54
11.04	41.74	1022.6	77.51	477.2
14.45	52.75	1023.97	63.59	459.85
13.97	38.47	1015.15	55.28	464.3
17.76	42.42	1009.09	66.26	468.27
5.41	40.07	1019.16	64.77	495.24
7.76	42.28	1008.52	83.31	483.8
27.23	63.9	1014.3	47.19	443.61
27.36	48.6	1003.18	54.93	436.06
27.47	70.72	1009.97	74.62	443.25
14.6	39.31	1011.11	72.52	464.16
7.91	39.96	1023.57	88.44	475.52
5.81	35.79	1012.14	92.28	484.41
30.53	65.18	1012.69	4

`dbutils.fs` has its own help facility, which we can use to see the various available functions.

In [0]:
dbutils.fs.help()

dbutils.fs provides utilities for working with FileSystems. Most methods in
this package can take either a DBFS path (e.g., "/foo" or "dbfs:/foo"), or
another FileSystem URI.

For more info about a method, use dbutils.fs.help("methodName") .

In notebooks, you can also use the %fs shorthand to access DBFS. The %fs shorthand maps
straightforwardly onto dbutils calls. For example, "%fs head --maxBytes=10000 /file/path"
translates into "dbutils.fs.head("/file/path", maxBytes = 10000)".
 mount mount(source: String, mountPoint: String, encryptionType: String = "", owner: String = null, extraConfigs: Map = Map.empty[String, String]): boolean -> Mounts the given source directory into DBFS at the given mount point mounts: Seq -> Displays information about what is mounted within DBFS refreshMounts: boolean -> Forces all machines in this cluster to refresh their mount cache, ensuring they receive the most recent information unmount(mountPoint: String): boolean -> Deletes a DBFS mount point updateMount(source: String, mountPoint: String, encryptionType: String = "", owner: String = null, extraConfigs: Map = Map.empty[String, String]): boolean -> Similar to mount(), but updates an existing mount point (if present) instead of creating a new one fsutils cp(from: String, to: String, recurse: boolean = false): boolean -> Copies a file or directory, possibly across FileSystems head(file: String, maxBytes: int = 65536): String -> Returns up to the first 'maxBytes' bytes of the given file as a String encoded in UTF-8 ls(dir: String): Seq -> Lists the contents of a directory mkdirs(dir: String): boolean -> Creates the given directory if it does not exist, also creating any necessary parent directories mv(from: String, to: String, recurse: boolean = false): boolean -> Moves a file or directory, possibly across FileSystems put(file: String, contents: String, overwrite: boolean = false): boolean -> Writes the given String out to a file, encoded in UTF-8 rm(dir: String, recurse: boolean = false): boolean -> Removes a file or directory

### Exercise 2(a)

Now, let's use PySpark instead to print the first 5 lines of the data.

*Hint*: First create an RDD from the data by using [`sc.textFile("dbfs:/databricks-datasets/power-plant/data")`](https://spark.apache.org/docs/1.6.2/api/python/pyspark.html#pyspark.SparkContext.textFile) to read the data into an RDD.

In [0]:
# TODO: Uncomment the line below and replace <FILL IN> with appropriate code to print the data

url = "https://raw.githubusercontent.com/10605/data/master/hw2/Sheet"

from pyspark import SparkFiles
sc.addFile(url+"1.tsv"); sc.addFile(url+"2.tsv"); sc.addFile(url+"3.tsv"); sc.addFile(url+"4.tsv"); sc.addFile(url+"5.tsv")

rawTextRdd = sc.textFile("file://" + SparkFiles.getRootDirectory(), 8)

# # Print the first five lines
for line in rawTextRdd.take(5):
    print(line)

AT	V	AP	RH	PE
23.25	71.29	1008.05	71.36	442.21
13.87	42.99	1007.45	81.52	471.12
16.91	43.96	1013.32	79.87	465.86
10.09	37.14	1012.99	72.59	473.66


From our initial exploration of a sample of the data, we can make several observations for the ETL process:
  - The data is a set of .tsv (Tab Seperated Values) files (i.e., each row of the data is separated using tabs)
  - There is a header row, which is the name of the columns
  - It looks like the type of the data in each column is consistent (i.e., each column is of type double)

Our schema definition from UCI appears below:
- AT = Atmospheric Temperature in C
- V = Exhaust Vacuum Speed
- AP = Atmospheric Pressure
- RH = Relative Humidity
- PE = Power Output.  This is the value we are trying to predict given the measurements above.

We are ready to create a DataFrame from the TSV data. Spark does not have a native method for performing this operation, however we can use [spark-csv](https://spark-packages.org/package/databricks/spark-csv), a third-party package from [SparkPackages](https://spark-packages.org/). The documentation and source code for [spark-csv](https://spark-packages.org/package/databricks/spark-csv) can be found on [GitHub](https://github.com/databricks/spark-csv). The Python API can be found [here](https://github.com/databricks/spark-csv#python-api).

(**Note**: In Spark 2.0, the CSV package is built into the DataFrame API.)

To use the [spark-csv](https://spark-packages.org/package/databricks/spark-csv) package, we use the [sqlContext.read.format()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrameReader.format) method to specify the input data source format: `'com.databricks.spark.csv'`

We can provide the [spark-csv](https://spark-packages.org/package/databricks/spark-csv) package with options using the [options()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrameReader.options) method. The available options are listed in the GitHub documentation [here](https://github.com/databricks/spark-csv#features).

We will use the following three options:
- `delimiter` because our data is tab delimited
- `header` because our data has a header row
- `inferschema` because we believe that all of the data is double values, so the package can dynamically infer the type of each column. *Note that this will require two pass over the data.*


The last component of creating the DataFrame is to specify the location of the data source using the [load()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrameReader.load) method: `"/databricks-datasets/power-plant/data"`

Putting everything together, we will use an operation of the following form:

  `sqlContext.read.format().options().load()`

### Exercise 2(b)

**To Do:** Create a DataFrame from the data.

*Hint:* Use the above template and fill in each of the methods.

In [0]:
# TODO: Uncoment the line below and replace <FILL_IN> with the appropriate code.

powerPlantDF = sqlContext.read.format('com.databricks.spark.csv').options(delimiter='\t', header='true', inferschema='true').load("file://" + SparkFiles.getRootDirectory())
powerPlantDF.show()
# YOUR CODE HERE
# Before submitting to GradeScope please replace the argument to the load() method with: "file://" + SparkFiles.getRootDirectory()

+-----+-----+-------+-----+------+
|   AT|    V|     AP|   RH|    PE|
+-----+-----+-------+-----+------+
|14.96|41.76|1024.07|73.17|463.26|
|25.18|62.96|1020.04|59.08|444.37|
| 5.11| 39.4|1012.16|92.14|488.56|
|20.86|57.32|1010.24|76.64|446.48|
|10.82| 37.5|1009.23|96.62| 473.9|
|26.27|59.44|1012.23|58.77|443.67|
|15.89|43.96|1014.02|75.24|467.35|
| 9.48|44.71|1019.12|66.43|478.42|
|14.64| 45.0|1021.78|41.25|475.98|
|11.74|43.56|1015.14|70.72| 477.5|
|17.99|43.72|1008.64|75.04|453.02|
|20.14|46.93|1014.66|64.22|453.99|
|24.34| 73.5|1011.31|84.15|440.29|
|25.71|58.59|1012.77|61.83|451.28|
|26.19|69.34|1009.48|87.59|433.99|
|21.42|43.79|1015.76|43.08|462.19|
|18.21| 45.0|1022.86|48.84|467.54|
|11.04|41.74| 1022.6|77.51| 477.2|
|14.45|52.75|1023.97|63.59|459.85|
|13.97|38.47|1015.15|55.28| 464.3|
+-----+-----+-------+-----+------+
only showing top 20 rows



In [0]:
# TEST
from nose.tools import assert_equal, assert_true
expected = set([(s, 'double') for s in ('AP', 'AT', 'PE', 'RH', 'V')])
print(powerPlantDF.dtypes)
assert_equal(expected, set(powerPlantDF.dtypes), "Incorrect schema for powerPlantDF")

[('AT', 'double'), ('V', 'double'), ('AP', 'double'), ('RH', 'double'), ('PE', 'double')]


Check the names and types of the columns using the [dtypes](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrame.dtypes) method.

In [0]:
print (powerPlantDF.dtypes)

[('AT', 'double'), ('V', 'double'), ('AP', 'double'), ('RH', 'double'), ('PE', 'double')]


We can examine the data using the display() method.

In [0]:
display(powerPlantDF)

AT V AP RH PE 14.96 41.76 1024.07 73.17 463.26 25.18 62.96 1020.04 59.08 444.37 5.11 39.4 1012.16 92.14 488.56 20.86 57.32 1010.24 76.64 446.48 10.82 37.5 1009.23 96.62 473.9 26.27 59.44 1012.23 58.77 443.67 15.89 43.96 1014.02 75.24 467.35 9.48 44.71 1019.12 66.43 478.42 14.64 45.0 1021.78 41.25 475.98 11.74 43.56 1015.14 70.72 477.5 17.99 43.72 1008.64 75.04 453.02 20.14 46.93 1014.66 64.22 453.99 24.34 73.5 1011.31 84.15 440.29 25.71 58.59 1012.77 61.83 451.28 26.19 69.34 1009.48 87.59 433.99 21.42 43.79 1015.76 43.08 462.19 18.21 45.0 1022.86 48.84 467.54 11.04 41.74 1022.6 77.51 477.2 14.45 52.75 1023.97 63.59 459.85 13.97 38.47 1015.15 55.28 464.3 17.76 42.42 1009.09 66.26 468.27 5.41 40.07 1019.16 64.77 495.24 7.76 42.28 1008.52 83.31 483.8 27.23 63.9 1014.3 47.19 443.61 27.36 48.6 1003.18 54.93 436.06 27.47 70.72 1009.97 74.62 443.25 14.6 39.31 1011.11 72.52 464.16 7.91 39.96 1023.57 88.44 475.52 5.81 35.79 1012.14 92.28 484.41 30.53 65.18 1012.69 41.85 437.89 23.87 63.94 1019.02 44.28 445.11 26.09 58.41 1013.64 64.58 438.86 29.27 66.85 1011.11 63.25 440.98 27.38 74.16 1010.08 78.61 436.65 24.81 63.94 1018.76 44.51 444.26 12.75 44.03 1007.29 89.46 465.86 24.66 63.73 1011.4 74.52 444.37 16.38 47.45 1010.08 88.86 450.69 13.91 39.35 1014.69 75.51 469.02 23.18 51.3 1012.04 78.64 448.86 22.47 47.45 1007.62 76.65 447.14 13.39 44.85 1017.24 80.44 469.18 9.28 41.54 1018.33 79.89 482.8 11.82 42.86 1014.12 88.28 476.7 10.27 40.64 1020.63 84.6 474.99 22.92 63.94 1019.28 42.69 444.22 16.0 37.87 1020.24 78.41 461.33 21.22 43.43 1010.96 61.07 448.06 13.46 44.71 1014.51 50.0 474.6 9.39 40.11 1029.14 77.29 473.05 31.07 73.5 1010.58 43.66 432.06 12.82 38.62 1018.71 83.8 467.41 32.57 78.92 1011.6 66.47 430.12 8.11 42.18 1014.82 93.09 473.62 13.92 39.39 1012.94 80.52 471.81 23.04 59.43 1010.23 68.99 442.99 27.31 64.44 1014.65 57.27 442.77 5.91 39.33 1010.18 95.53 491.49 25.26 61.08 1013.68 71.72 447.46 27.97 58.84 1002.25 57.88 446.11 26.08 52.3 1007.03 63.34 442.44 29.01 65.71 1013.61 48.07 446.22 12.18 40.1 1016.67 91.87 471.49 13.76 45.87 1008.89 87.27 463.5 25.5 58.79 1016.02 64.4 440.01 28.26 65.34 1014.56 43.4 441.03 21.39 62.96 1019.49 72.24 452.68 7.26 40.69 1020.43 90.22 474.91 10.54 34.03 1018.71 74.0 478.77 27.71 74.34 998.14 71.85 434.2 23.11 68.3 1017.83 86.62 437.91 7.51 41.01 1024.61 97.41 477.61 26.46 74.67 1016.65 84.44 431.65 29.34 74.34 998.58 81.55 430.57 10.32 42.28 1008.82 75.66 481.09 22.74 61.02 1009.56 79.41 445.56 13.48 39.85 1012.71 58.91 475.74 25.52 69.75 1010.36 90.06 435.12 21.58 67.25 1017.39 79.0 446.15 27.66 76.86 1001.31 69.47 436.64 26.96 69.45 1013.89 51.47 436.69 12.29 42.18 1016.53 83.13 468.75 15.86 43.02 1012.18 40.33 466.6 13.87 45.08 1024.42 81.69 465.48 24.09 73.68 1014.93 94.55 441.34 20.45 69.45 1012.53 91.81 441.83 15.07 39.3 1019.0 63.62 464.7 32.72 69.75 1009.6 49.35 437.99 18.23 58.96 1015.55 69.61 459.12 35.56 68.94 1006.56 38.75 429.69 18.36 51.43 1010.57 90.17 459.8 26.35 64.05 1009.81 81.24 433.63 25.92 60.95 1014.62 48.46 442.84 8.01 41.66 1014.49 76.72 485.13 19.63 52.72 1025.09 51.16 459.12 20.02 67.32 1012.05 76.34 445.31 10.08 40.72 1022.7 67.3 480.8 27.23 66.48 1005.23 52.38 432.55 23.37 63.77 1013.42 76.44 443.86 18.74 59.21 1018.3 91.55 449.77 14.81 43.69 1017.19 71.9 470.71 23.1 51.3 1011.93 80.05 452.17 10.72 41.38 1021.6 63.77 478.29 29.46 71.94 1006.96 62.26 428.54 8.1 40.64 1020.66 89.04 478.27 27.29 62.66 1007.63 58.02 439.58 17.1 49.69 1005.53 81.82 457.32 11.49 44.2 1018.79 91.14 475.51 23.69 65.59 1010.85 88.92 439.66 13.51 40.89 1011.03 84.83 471.99 9.64 39.35 1015.1 91.76 479.81 25.65 78.92 1010.83 86.56 434.78 21.59 61.87 1011.18 57.21 446.58 27.98 58.33 1013.92 54.25 437.76 18.8 39.72 1001.24 63.8 459.36 18.28 44.71 1016.99 33.71 462.28 13.55 43.48 1016.08 67.25 464.33 22.99 46.21 1010.71 60.11 444.36 23.94 59.39 1014.32 74.55 438.64 13.74 34.03 1018.69 67.34 470.49 21.3 41.1 1001.86 42.75 455.13 27.54 66.93 1017.06 55.2 450.22 24.81 63.73 1009.34 83.61 440.43 4.9

### Exercise 2(c)

Instead of having [spark-csv](https://spark-packages.org/package/databricks/spark-csv) infer the types of the columns, we can specify the schema as a [DataType](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.types.DataType), which is a list of [StructField](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.types.StructType).
You can find a list of types in the [pyspark.sql.types](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#module-pyspark.sql.types) module. For our data, we will use [DoubleType()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.types.DoubleType).
For example, to specify that a column's name and type, we use: `StructField(`_name_`,` _type_`, True)`. (The third parameter, `True`, signifies that the column is nullable.)

Create a custom schema for the power plant data.

In [0]:
# TO DO: Uncomment the lines and fill in the custom schema.
from pyspark.sql.types import *

# Custom Schema for Power Plant
customSchema = StructType([ \
    StructField("AT", DoubleType(), True),
    StructField("V", DoubleType(), True),
    StructField("AP", DoubleType(), True),
    StructField("RH", DoubleType(), True),
    StructField("PE", DoubleType(), True)
                          ])

In [0]:
# TEST
assert_equal(set([f.name for f in customSchema.fields]), set(['AT', 'V', 'AP', 'RH', 'PE']), 'Incorrect column names in schema.')
assert_equal(set([f.dataType for f in customSchema.fields]), set([DoubleType(), DoubleType(), DoubleType(), DoubleType(), DoubleType()]), 'Incorrect column types in schema.')

### Exercise 2(d)

Now, let's use the schema to read the data. To do this, we will modify the earlier `sqlContext.read.format` step. We can specify the schema by:
- Adding `schema = customSchema` to the load method (use a comma and add it after the file name)
- Removing the `inferschema='true'`option because we are explicitly specifying the schema

In [0]:
# TODO: Uncomment the line and use the schema you created above to load the data again.
altPowerPlantDF = sqlContext.read.format('com.databricks.spark.csv').options(delimiter='\t', header='true').schema(customSchema).load("file://" + SparkFiles.getRootDirectory())

# YOUR CODE HERE
# Before submitting to GradeScope please replace the argument to the load() method with: "file://" + SparkFiles.getRootDirectory()


In [0]:
# TEST
expected = set([(s, 'double') for s in ('AP', 'AT', 'PE', 'RH', 'V')])
assert_equal(expected, set(altPowerPlantDF.dtypes), "Incorrect schema for powerPlantDF")

Note that no Spark jobs are launched this time. That is because we specified the schema, so the [spark-csv](https://spark-packages.org/package/databricks/spark-csv) package does not have to read the data to infer the schema. We can use the [dtypes](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrame.dtypes) method to examine the names and types of the columns. They should be identical to the names and types of the columns that were earlier inferred from the data.

When you run the following cell, data would not be read.

In [0]:
print (altPowerPlantDF.dtypes)

[('AT', 'double'), ('V', 'double'), ('AP', 'double'), ('RH', 'double'), ('PE', 'double')]


Now we can examine the data using the display() method. *Note that this operation will cause the data to be read and the DataFrame will be created.*

In [0]:
display(altPowerPlantDF)

AT V AP RH PE null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null n

## Part 3: Explore Your Data
Now that your data is loaded, the next step is to explore it and perform some basic analysis and visualizations.

This is a step that you should always perform **before** trying to fit a model to the data, as this step will often lead to important insights about your data.

### Exercise 3(a)
First, let's register our DataFrame as an SQL table named `power_plant`.  Because you may run this lab multiple times, we'll take the precaution of removing any existing tables first.

We can delete any existing `power_plant` SQL table using the SQL command: `DROP TABLE IF EXISTS power_plant` (we also need to to delete any Hive data associated with the table, which we can do with a Databricks file system operation).

Once any prior table is removed, we can register our DataFrame as a SQL table using [sqlContext.registerDataFrameAsTable()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.SQLContext.registerDataFrameAsTable).

**ToDo:** Execute the prepared code in the following cell.

In [0]:
# uncomment to delete hive data in databricks:
# dbutils.fs.rm("dbfs:/user/hive/warehouse/power_plant", True)
# Be sure to leave it commented BEFORE UPLOADING TO Gradescope

sqlContext.sql("DROP TABLE IF EXISTS power_plant")
sqlContext.registerDataFrameAsTable(powerPlantDF, "power_plant")

### Exercise 3(b)

Now that our DataFrame exists as a SQL table, we can explore it using SQL commands.

To execute SQL in a cell, we use the `%sql` operator. The following cell is an example of using SQL to query the rows of the SQL table.

**NOTE**: `%sql` is a Databricks-only command. It calls `sqlContext.sql()` and passes the results to the Databricks-only `display()` function. These two statements are equivalent:

`%sql SELECT * FROM power_plant`

`display(sqlContext.sql("SELECT * FROM power_plant"))`

While `%sql` can be run on Databricks it CANNOT be run on Gradescope. As such before uploading to Gradescope be sure to comment out the cells starting this way.

**ToDo**: Execute the prepared code in the following cell.

In [0]:
#%sql
#SELECT * FROM power_plant

# Comment out this cell before uploading to Gradescope

### Exercise 3(c)

Use the SQL `desc` command to describe the schema, by executing the following cell.

In [0]:
#%sql desc power_plant

# Comment out this cell before uploading to Gradescope

**Schema Definition**

Once again, here's our schema definition:

- AT = Atmospheric Temperature in C
- V = Exhaust Vacuum Speed
- AP = Atmospheric Pressure
- RH = Relative Humidity
- PE = Power Output

PE is our label or target. This is the value we are trying to predict given the measurements.

*Reference [UCI Machine Learning Repository Combined Cycle Power Plant Data Set](https://archive.ics.uci.edu/ml/datasets/Combined+Cycle+Power+Plant)*

Let's perform some basic statistical analyses of all the columns.

We can get the DataFrame associated with a SQL table by using the [sqlContext.table()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrameReader.table) method and passing in the name of the SQL table. Then, we can use the DataFrame [describe()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrame.describe) method with no arguments to compute some basic statistics for each column like count, mean, max, min and standard deviation.

In [0]:
#df = sqlContext.table("power_plant")
#display(df.describe())
# Comment out this cell before uploading to Gradescope

## Part 4: Visualize Your Data

To understand our data, we will look for correlations between features and the label.  This can be important when choosing a model.  E.g., if features and a label are linearly correlated, a linear model like Linear Regression can do well; if the relationship is very non-linear, more complex models such as random forests can be better. We can use Databrick's built in visualization to view each of our predictors in relation to the label column as a scatter plot to see the correlation between the predictors and the label.

### Exercise 4(a)

** Add figures to the following: **
Let's see if there is a corellation between Temperature and Power Output. We can use a dataframe consisting of only the Temperature (AT) and Power (PE) columns, and then use a scatter plot with Temperature on the X axis and Power on the Y axis to visualize the relationship (if any) between Temperature and Power.


Perform the following steps:

- Run the following cell
- Click on the drop down next to the "Bar chart" icon and select "Scatter" to turn the table into a Scatter plot

<img src="http://spark-mooc.github.io/web-assets/images/cs110x/change-plot-type-scatter.png" style="border: 1px solid #999999"/>

- Click on "Plot Options..."
- In the Values box, click on "Temperature" and drag it before "Power", as shown below:

<img src="http://spark-mooc.github.io/web-assets/images/cs110x/customize-plot-scatter.png" style="border: 1px solid #999999"/>

- Apply your changes by clicking the Apply button
- Increase the size of the graph by clicking and dragging the size control

In [0]:
# TODO: Uncomment the template below and replace <FILL IN> with appropriate code
from pyspark.sql.functions import col
display(powerPlantDF.select(col("AT").alias("Temperature"), col("PE").alias("Power")))


Temperature Power 14.96 463.26 25.18 444.37 5.11 488.56 20.86 446.48 10.82 473.9 26.27 443.67 15.89 467.35 9.48 478.42 14.64 475.98 11.74 477.5 17.99 453.02 20.14 453.99 24.34 440.29 25.71 451.28 26.19 433.99 21.42 462.19 18.21 467.54 11.04 477.2 14.45 459.85 13.97 464.3 17.76 468.27 5.41 495.24 7.76 483.8 27.23 443.61 27.36 436.06 27.47 443.25 14.6 464.16 7.91 475.52 5.81 484.41 30.53 437.89 23.87 445.11 26.09 438.86 29.27 440.98 27.38 436.65 24.81 444.26 12.75 465.86 24.66 444.37 16.38 450.69 13.91 469.02 23.18 448.86 22.47 447.14 13.39 469.18 9.28 482.8 11.82 476.7 10.27 474.99 22.92 444.22 16.0 461.33 21.22 448.06 13.46 474.6 9.39 473.05 31.07 432.06 12.82 467.41 32.57 430.12 8.11 473.62 13.92 471.81 23.04 442.99 27.31 442.77 5.91 491.49 25.26 447.46 27.97 446.11 26.08 442.44 29.01 446.22 12.18 471.49 13.76 463.5 25.5 440.01 28.26 441.03 21.39 452.68 7.26 474.91 10.54 478.77 27.71 434.2 23.11 437.91 7.51 477.61 26.46 431.65 29.34 430.57 10.32 481.09 22.74 445.56 13.48 475.74 25.52 435.12 21.58 446.15 27.66 436.64 26.96 436.69 12.29 468.75 15.86 466.6 13.87 465.48 24.09 441.34 20.45 441.83 15.07 464.7 32.72 437.99 18.23 459.12 35.56 429.69 18.36 459.8 26.35 433.63 25.92 442.84 8.01 485.13 19.63 459.12 20.02 445.31 10.08 480.8 27.23 432.55 23.37 443.86 18.74 449.77 14.81 470.71 23.1 452.17 10.72 478.29 29.46 428.54 8.1 478.27 27.29 439.58 17.1 457.32 11.49 475.51 23.69 439.66 13.51 471.99 9.64 479.81 25.65 434.78 21.59 446.58 27.98 437.76 18.8 459.36 18.28 462.28 13.55 464.33 22.99 444.36 23.94 438.64 13.74 470.49 21.3 455.13 27.54 450.22 24.81 440.43 4.97 482.98 15.22 460.44 23.88 444.97 33.01 433.94 25.98 439.73 28.18 434.48 21.67 442.33 17.67 457.67 21.37 454.66 28.69 432.21 16.61 457.66 27.91 435.21 20.97 448.22 10.8 475.51 20.61 446.53 25.45 441.3 30.16 433.54 4.99 472.52 10.51 474.77 33.79 435.1 21.34 450.74 23.4 442.7 32.21 426.56 14.26 463.71 27.71 447.06 21.95 452.27 25.76 445.78 23.68 438.65 8.28 480.15 23.44 447.19 25.32 443.04 3.94 488.81 17.3 455.75 18.2 455.86 21.43 457.68 11.16 479.11 30.38 432.84 23.36 448.37 21.69 447.06 23.62 443.53 21.87 445.21 29.25 441.7 20.03 450.93 18.14 451.44 24.23 441.29 18.11 458.85 6.57 481.46 12.56 467.19 13.4 461.54 27.1 439.08 14.28 467.22 16.29 468.8 31.24 426.93 10.57 474.65 13.8 468.97 25.3 433.97 18.06 450.53 25.42 444.51 15.07 469.03 11.75 466.56 20.23 457.57 27.31 440.13 28.57 433.24 17.9 452.55 23.83 443.29 27.92 431.76 17.34 454.97 17.94 456.7 6.4 486.03 11.78 472.79 20.28 452.03 21.04 443.41 25.11 441.93 30.28 432.64 8.14 480.25 16.86 466.68 6.25 494.39 22.35 454.72 17.98 448.71 21.19 469.76 20.94 450.71 24.23 444.01 19.18 453.2 20.88 450.87 23.67 441.73 14.12 465.09 25.23 447.28 6.54 491.16 20.08 450.98 24.67 446.3 27.82 436.48 15.55 460.84 24.26 442.56 13.45 467.3 11.06 479.13 24.91 441.15 22.39 445.52 11.95 475.4 14.85 469.3 10.11 463.57 23.67 445.32 16.14 461.03 15.11 466.74 24.14 444.04 30.08 434.01 14.77 465.23 27.6 440.6 13.89 466.74 26.85 433.48 12.41 473.59 13.08 474.81 18.93 454.75 20.5 452.94 30.72 435.83 7.55 482.19 13.49 466.66 15.62 462.59 24.8 447.82 10.03 462.73 22.43 447.98 14.95 462.72 24.78 442.42 23.2 444.69 14.01 466.7 19.4 453.84 30.15 436.92 6.91 486.37 29.04 440.43 26.02 446.82 5.89 484.91 26.52 437.76 28.53 438.91 16.59 464.19 22.95 442.19 23.96 446.86 17.48 457.15 6.69 482.57 10.25 476.03 28.87 428.89 12.04 472.7 22.58 445.6 15.12 464.78 25.48 440.42 27.87 428.41 23.72 438.5 25.0 438.28 8.42 476.29 22.46 448.46 29.92 438.99 11.68 471.8 14.04 471.81 19.86 449.82 25.99 442.14 23.42 441.46 10.6 477.62 20.97 446.76 14.14 472.52 8.56 471.58 24.86 440.85 29.0 431.37 27.59 437.33 10.45 469.22 8.51 471.11 29.82 439.17 22.56 445.33 11.38 473.71 20.25 452.66 22.42 440.99 14.85 467.42 25.62 444.14 19.85 457.17 13.67 467.87 24.39 442.04 16.07 471.36 11.6 460.7 31.38 431.33 29.91 432.6 19.67 447.61 27.18 443.87 21.39 446.87 10.45 465.74 19.46 447.86 23.55 447.65 23.35 437.87 9.26 483.51 10.3 479.65 20.94 455.16 23.13 431.91 12.77 470.68 28.29 429.28 19.13 

Databricks visualization. Run in Databricks to view.

It looks like there is strong linear correlation between Temperature and Power Output.

** ASIDE: A quick physics lesson**: This correlation is to be expected as the second law of thermodynamics puts a fundamental limit on the [thermal efficiency](https://en.wikipedia.org/wiki/Thermal_efficiency) of all heat-based engines. The limiting factors are:
 - The temperature at which the heat enters the engine \\( T_{H} \\)
 - The temperature of the environment into which the engine exhausts its waste heat \\( T_C \\)

Our temperature measurements are the temperature of the environment. From [Carnot's theorem](https://en.wikipedia.org/wiki/Carnot%27s_theorem_%28thermodynamics%29), no heat engine working between these two temperatures can exceed the Carnot Cycle efficiency:
\\[ n_{th} \le 1 - \frac{T_C}{T_H}  \\]

Note that as the environmental temperature increases, the efficiency decreases -- _this is the effect that we see in the above graph._

### Exercise 4(b)

Use DataFrame to create a scatter plot of Power(PE) as a function of ExhaustVacuum (V).
Name the y-axis "Power" and the x-axis "ExhaustVacuum"

In [0]:
# TODO: Uncomment the template below and replace <FILL IN> with appropriate code
display(powerPlantDF.select(col("V").alias("ExhaustVacuum"), col("PE").alias("Power")))


ExhaustVacuum Power 41.76 463.26 62.96 444.37 39.4 488.56 57.32 446.48 37.5 473.9 59.44 443.67 43.96 467.35 44.71 478.42 45.0 475.98 43.56 477.5 43.72 453.02 46.93 453.99 73.5 440.29 58.59 451.28 69.34 433.99 43.79 462.19 45.0 467.54 41.74 477.2 52.75 459.85 38.47 464.3 42.42 468.27 40.07 495.24 42.28 483.8 63.9 443.61 48.6 436.06 70.72 443.25 39.31 464.16 39.96 475.52 35.79 484.41 65.18 437.89 63.94 445.11 58.41 438.86 66.85 440.98 74.16 436.65 63.94 444.26 44.03 465.86 63.73 444.37 47.45 450.69 39.35 469.02 51.3 448.86 47.45 447.14 44.85 469.18 41.54 482.8 42.86 476.7 40.64 474.99 63.94 444.22 37.87 461.33 43.43 448.06 44.71 474.6 40.11 473.05 73.5 432.06 38.62 467.41 78.92 430.12 42.18 473.62 39.39 471.81 59.43 442.99 64.44 442.77 39.33 491.49 61.08 447.46 58.84 446.11 52.3 442.44 65.71 446.22 40.1 471.49 45.87 463.5 58.79 440.01 65.34 441.03 62.96 452.68 40.69 474.91 34.03 478.77 74.34 434.2 68.3 437.91 41.01 477.61 74.67 431.65 74.34 430.57 42.28 481.09 61.02 445.56 39.85 475.74 69.75 435.12 67.25 446.15 76.86 436.64 69.45 436.69 42.18 468.75 43.02 466.6 45.08 465.48 73.68 441.34 69.45 441.83 39.3 464.7 69.75 437.99 58.96 459.12 68.94 429.69 51.43 459.8 64.05 433.63 60.95 442.84 41.66 485.13 52.72 459.12 67.32 445.31 40.72 480.8 66.48 432.55 63.77 443.86 59.21 449.77 43.69 470.71 51.3 452.17 41.38 478.29 71.94 428.54 40.64 478.27 62.66 439.58 49.69 457.32 44.2 475.51 65.59 439.66 40.89 471.99 39.35 479.81 78.92 434.78 61.87 446.58 58.33 437.76 39.72 459.36 44.71 462.28 43.48 464.33 46.21 444.36 59.39 438.64 34.03 470.49 41.1 455.13 66.93 450.22 63.73 440.43 42.85 482.98 50.88 460.44 54.2 444.97 68.67 433.94 73.18 439.73 73.88 434.48 60.84 442.33 45.09 457.67 57.76 454.66 67.25 432.21 43.77 457.66 63.76 435.21 47.43 448.22 41.66 475.51 62.91 446.53 57.32 441.3 69.34 433.54 39.04 472.52 44.78 474.77 69.05 435.1 59.8 450.74 65.06 442.7 68.14 426.56 42.32 463.71 66.93 447.06 57.76 452.27 63.94 445.78 68.3 438.65 40.77 480.15 62.52 447.19 48.41 443.04 39.9 488.81 57.76 455.75 49.39 455.86 46.97 457.68 40.05 479.11 74.16 432.84 62.52 448.37 47.45 447.06 49.21 443.53 61.45 445.21 66.51 441.7 66.86 450.93 49.78 451.44 56.89 441.29 44.85 458.85 43.65 481.46 43.41 467.19 41.58 461.54 52.84 439.08 42.74 467.22 44.34 468.8 71.98 426.93 37.73 474.65 44.21 468.97 71.58 433.97 50.16 450.53 59.04 444.51 40.69 469.03 71.14 466.56 52.05 457.57 59.54 440.13 69.84 433.24 43.72 452.55 71.37 443.29 74.99 431.76 44.78 454.97 63.07 456.7 39.9 486.03 39.96 472.79 57.25 452.03 54.2 443.41 67.32 441.93 70.98 432.64 36.24 480.25 39.63 466.68 40.07 494.39 54.42 454.72 56.85 448.71 42.48 469.76 44.89 450.71 58.79 444.01 58.2 453.2 57.85 450.87 63.86 441.73 39.52 465.09 64.63 447.28 39.33 491.16 62.52 450.98 63.56 446.3 79.74 436.48 42.03 460.84 69.51 442.56 41.49 467.3 40.64 479.13 52.3 441.15 59.04 445.52 40.69 475.4 40.69 469.3 41.62 463.57 68.67 445.32 44.21 461.03 43.13 466.74 59.87 444.04 67.25 434.01 44.9 465.23 69.34 440.6 44.84 466.74 75.6 433.48 40.96 473.59 41.74 474.81 44.06 454.75 49.69 452.94 69.13 435.83 39.22 482.19 44.47 466.66 40.12 462.59 64.63 447.82 41.62 462.73 63.21 447.98 39.31 462.72 58.46 442.42 48.41 444.69 39.0 466.7 64.63 453.84 67.32 436.92 36.08 486.37 60.07 440.43 63.07 446.82 39.48 484.91 71.64 437.76 68.08 438.91 39.54 464.19 67.79 442.19 47.43 446.86 44.2 457.15 43.65 482.57 41.26 476.03 72.58 428.89 40.23 472.7 52.3 445.6 52.05 464.78 58.95 440.42 70.79 428.41 70.47 438.5 59.43 438.28 40.64 476.29 58.49 448.46 57.19 438.99 39.22 471.8 42.44 471.81 59.14 449.82 68.08 442.14 58.79 441.46 40.22 477.62 61.87 446.76 39.82 472.52 40.71 471.58 72.39 440.85 77.54 431.37 71.97 437.33 40.71 469.22 40.78 471.11 66.51 439.17 62.26 445.33 39.22 473.71 57.76 452.66 59.43 440.99 38.91 467.42 58.82 444.14 56.53 457.17 54.3 467.87 70.72 442.04 44.58 471.36 39.1 460.7 70.83 431.33 76.86 432.6 59.39 447.61 64.79 443.87 52.3 446.87 41.01 465.74 56.89 447.86 62.96 447.65 63.47 437.87 41.66 483.51 41.46 479.65 58.16 455.16 71.25 431.91 41

Databricks visualization. Run in Databricks to view.

### Exercise 4(c)

Let's continue exploring the relationships (if any) between the variables and Power Output.

Use DataFrame to create a scatter plot of Power(PE) as a function of Pressure (AP).
Name the y-axis "Power" and the x-axis "Pressure"

In [0]:
# TODO: Uncomment the template below and replace <FILL IN> with appropriate code
display(powerPlantDF.select(col("AP").alias("Pressure"), col("PE").alias("Power")))


Pressure Power 1024.07 463.26 1020.04 444.37 1012.16 488.56 1010.24 446.48 1009.23 473.9 1012.23 443.67 1014.02 467.35 1019.12 478.42 1021.78 475.98 1015.14 477.5 1008.64 453.02 1014.66 453.99 1011.31 440.29 1012.77 451.28 1009.48 433.99 1015.76 462.19 1022.86 467.54 1022.6 477.2 1023.97 459.85 1015.15 464.3 1009.09 468.27 1019.16 495.24 1008.52 483.8 1014.3 443.61 1003.18 436.06 1009.97 443.25 1011.11 464.16 1023.57 475.52 1012.14 484.41 1012.69 437.89 1019.02 445.11 1013.64 438.86 1011.11 440.98 1010.08 436.65 1018.76 444.26 1007.29 465.86 1011.4 444.37 1010.08 450.69 1014.69 469.02 1012.04 448.86 1007.62 447.14 1017.24 469.18 1018.33 482.8 1014.12 476.7 1020.63 474.99 1019.28 444.22 1020.24 461.33 1010.96 448.06 1014.51 474.6 1029.14 473.05 1010.58 432.06 1018.71 467.41 1011.6 430.12 1014.82 473.62 1012.94 471.81 1010.23 442.99 1014.65 442.77 1010.18 491.49 1013.68 447.46 1002.25 446.11 1007.03 442.44 1013.61 446.22 1016.67 471.49 1008.89 463.5 1016.02 440.01 1014.56 441.03 1019.49 452.68 1020.43 474.91 1018.71 478.77 998.14 434.2 1017.83 437.91 1024.61 477.61 1016.65 431.65 998.58 430.57 1008.82 481.09 1009.56 445.56 1012.71 475.74 1010.36 435.12 1017.39 446.15 1001.31 436.64 1013.89 436.69 1016.53 468.75 1012.18 466.6 1024.42 465.48 1014.93 441.34 1012.53 441.83 1019.0 464.7 1009.6 437.99 1015.55 459.12 1006.56 429.69 1010.57 459.8 1009.81 433.63 1014.62 442.84 1014.49 485.13 1025.09 459.12 1012.05 445.31 1022.7 480.8 1005.23 432.55 1013.42 443.86 1018.3 449.77 1017.19 470.71 1011.93 452.17 1021.6 478.29 1006.96 428.54 1020.66 478.27 1007.63 439.58 1005.53 457.32 1018.79 475.51 1010.85 439.66 1011.03 471.99 1015.1 479.81 1010.83 434.78 1011.18 446.58 1013.92 437.76 1001.24 459.36 1016.99 462.28 1016.08 464.33 1010.71 444.36 1014.32 438.64 1018.69 470.49 1001.86 455.13 1017.06 450.22 1009.34 440.43 1014.02 482.98 1014.19 460.44 1012.81 444.97 1005.2 433.94 1012.28 439.73 1005.89 434.48 1017.93 442.33 1014.26 457.67 1018.8 454.66 1017.71 432.21 1012.25 457.66 1010.27 435.21 1007.64 448.22 1013.79 475.51 1013.24 446.53 1011.7 441.3 1007.67 433.54 1020.45 472.52 1012.59 474.77 1001.62 435.1 1016.92 450.74 1014.32 442.7 1003.34 426.56 1016.0 463.71 1016.85 447.06 1018.02 452.27 1018.49 445.78 1017.93 438.65 1011.55 480.15 1016.46 447.19 1008.47 443.04 1008.06 488.81 1016.26 455.75 1018.83 455.86 1013.94 457.68 1014.95 479.11 1007.44 432.84 1016.18 448.37 1007.56 447.06 1014.1 443.53 1011.13 445.21 1015.53 441.7 1013.05 450.93 1002.95 451.44 1012.32 441.29 1014.48 458.85 1018.24 481.46 1016.93 467.19 1020.5 461.54 1006.28 439.08 1028.79 467.22 1019.49 468.8 1004.66 426.93 1024.36 474.65 1022.93 468.97 1010.18 433.97 1009.52 450.53 1011.98 444.51 1015.29 469.03 1019.36 466.56 1012.15 457.57 1006.24 440.13 1003.57 433.24 1008.64 452.55 1002.04 443.29 1005.47 431.76 1007.81 454.97 1012.42 456.7 1007.75 486.03 1011.37 472.79 1010.12 452.03 1012.26 443.41 1014.49 441.93 1007.51 432.64 1013.15 480.25 1004.47 466.68 1020.19 494.39 1012.46 454.72 1012.28 448.71 1013.43 469.76 1009.64 450.71 1009.8 444.01 1017.46 453.2 1012.39 450.87 1019.67 441.73 1018.41 465.09 1020.59 447.28 1011.54 491.16 1017.99 450.98 1013.75 446.3 1008.37 436.48 1017.41 460.84 1013.43 442.56 1020.19 467.3 1021.47 479.13 1008.72 441.15 1011.78 445.52 1015.62 475.4 1014.91 469.3 1017.17 463.57 1006.71 445.32 1020.36 461.03 1014.99 466.74 1018.47 444.04 1017.6 434.01 1020.5 465.23 1009.63 440.6 1023.66 466.74 1017.43 433.48 1023.36 473.59 1020.75 474.81 1017.58 454.75 1009.6 452.94 1009.94 435.83 1014.53 482.19 1030.46 466.66 1013.03 462.59 1020.69 447.82 1014.55 462.73 1012.06 447.98 1009.15 462.72 1016.82 442.42 1008.64 444.69 1016.73 466.7 1020.38 453.84 1013.83 436.92 1021.82 486.37 1015.42 440.43 1010.94 446.82 1005.11 484.91 1008.27 437.76 1013.27 438.91 1007.97 464.19 1009.89 442.19 1008.38 446.86 1018.89 457.15 1020.14 482.57 1007.44 476.03 1008.69 428.89 1018.07 472.7 1009.04 445.6 1014.63 464.78 1017.02 440.42 1003.96 428.41 1010.65 438.5 1007.84 438.28 10

Databricks visualization. Run in Databricks to view.

### Exercise 4(d)

Use DataFrame to create a scatter plot of Power(PE) as a function of Humidity (RH).
Name the y-axis "Power" and the x-axis "Humidity"

In [0]:
# TODO: Uncomment the template below and replace <FILL IN> with appropriate code
display(powerPlantDF.select(col("RH").alias("Humidity"), col("PE").alias("Power")))

Humidity Power 73.17 463.26 59.08 444.37 92.14 488.56 76.64 446.48 96.62 473.9 58.77 443.67 75.24 467.35 66.43 478.42 41.25 475.98 70.72 477.5 75.04 453.02 64.22 453.99 84.15 440.29 61.83 451.28 87.59 433.99 43.08 462.19 48.84 467.54 77.51 477.2 63.59 459.85 55.28 464.3 66.26 468.27 64.77 495.24 83.31 483.8 47.19 443.61 54.93 436.06 74.62 443.25 72.52 464.16 88.44 475.52 92.28 484.41 41.85 437.89 44.28 445.11 64.58 438.86 63.25 440.98 78.61 436.65 44.51 444.26 89.46 465.86 74.52 444.37 88.86 450.69 75.51 469.02 78.64 448.86 76.65 447.14 80.44 469.18 79.89 482.8 88.28 476.7 84.6 474.99 42.69 444.22 78.41 461.33 61.07 448.06 50.0 474.6 77.29 473.05 43.66 432.06 83.8 467.41 66.47 430.12 93.09 473.62 80.52 471.81 68.99 442.99 57.27 442.77 95.53 491.49 71.72 447.46 57.88 446.11 63.34 442.44 48.07 446.22 91.87 471.49 87.27 463.5 64.4 440.01 43.4 441.03 72.24 452.68 90.22 474.91 74.0 478.77 71.85 434.2 86.62 437.91 97.41 477.61 84.44 431.65 81.55 430.57 75.66 481.09 79.41 445.56 58.91 475.74 90.06 435.12 79.0 446.15 69.47 436.64 51.47 436.69 83.13 468.75 40.33 466.6 81.69 465.48 94.55 441.34 91.81 441.83 63.62 464.7 49.35 437.99 69.61 459.12 38.75 429.69 90.17 459.8 81.24 433.63 48.46 442.84 76.72 485.13 51.16 459.12 76.34 445.31 67.3 480.8 52.38 432.55 76.44 443.86 91.55 449.77 71.9 470.71 80.05 452.17 63.77 478.29 62.26 428.54 89.04 478.27 58.02 439.58 81.82 457.32 91.14 475.51 88.92 439.66 84.83 471.99 91.76 479.81 86.56 434.78 57.21 446.58 54.25 437.76 63.8 459.36 33.71 462.28 67.25 464.33 60.11 444.36 74.55 438.64 67.34 470.49 42.75 455.13 55.2 450.22 83.61 440.43 88.78 482.98 100.12 460.44 64.52 444.97 51.41 433.94 85.78 439.73 75.41 434.48 81.63 442.33 51.92 457.67 70.12 454.66 53.83 432.21 77.23 457.66 65.67 435.21 71.18 448.22 81.96 475.51 79.54 446.53 47.09 441.3 57.69 433.54 78.89 472.52 85.29 474.77 40.13 435.1 77.06 450.74 67.38 442.7 62.44 426.56 77.43 463.71 58.77 447.06 67.72 452.27 42.14 445.78 84.16 438.65 89.79 480.15 67.21 447.19 72.14 443.04 97.49 488.81 87.74 455.75 96.3 455.86 61.25 457.68 88.38 479.11 74.77 432.84 68.18 448.37 77.2 447.06 49.54 443.53 92.22 445.21 33.65 441.7 64.59 450.93 100.09 451.44 68.04 441.29 48.94 458.85 74.47 481.46 81.02 467.19 71.17 461.54 53.85 439.08 70.67 467.22 59.36 468.8 57.17 426.93 70.29 474.65 83.37 468.97 87.36 433.97 100.09 450.53 68.78 444.51 70.98 469.03 75.68 466.56 47.49 457.57 71.99 440.13 66.55 433.24 74.73 452.55 64.78 443.29 75.13 431.76 56.38 454.97 94.35 456.7 86.55 486.03 82.95 472.79 88.42 452.03 85.61 443.41 58.39 441.93 74.28 432.64 87.85 480.25 83.5 466.68 65.24 494.39 75.01 454.72 84.52 448.71 80.52 469.76 75.14 450.71 75.75 444.01 76.72 453.2 85.47 450.87 57.95 441.73 78.32 465.09 52.2 447.28 93.69 491.16 75.74 450.98 67.56 446.3 69.46 436.48 74.58 460.84 53.23 442.56 88.72 467.3 96.16 479.13 68.26 441.15 86.39 445.52 85.34 475.4 72.64 469.3 97.82 463.57 77.22 445.32 80.59 461.03 46.91 466.74 57.76 444.04 53.09 434.01 84.31 465.23 71.58 440.6 92.97 466.74 74.55 433.48 78.96 473.59 64.44 474.81 68.23 454.75 70.81 452.94 61.66 435.83 77.76 482.19 69.49 466.66 96.26 462.59 55.74 447.82 95.61 462.73 84.75 447.98 75.3 462.72 67.5 442.42 80.92 444.69 79.23 466.7 81.1 453.84 32.8 436.92 84.31 486.37 46.15 440.43 53.96 446.82 59.83 484.91 75.3 437.76 42.53 438.91 70.58 464.19 91.69 442.19 63.55 446.86 61.51 457.15 69.55 482.57 98.08 476.03 79.34 428.89 81.28 472.7 78.99 445.6 80.38 464.78 51.16 440.42 72.17 428.41 75.39 438.5 68.91 438.28 96.38 476.29 70.54 448.46 45.8 438.99 57.95 471.8 81.89 471.81 69.32 449.82 59.14 442.14 81.54 441.46 85.81 477.62 65.41 446.76 81.15 472.52 95.87 471.58 90.24 440.85 75.13 431.37 88.22 437.33 81.48 469.22 89.84 471.11 43.57 439.17 63.16 445.33 57.14 473.71 77.76 452.66 90.56 440.99 60.98 467.42 70.31 444.14 74.05 457.17 75.42 467.87 82.25 442.04 67.95 471.36 100.09 460.7 47.28 431.33 72.41 432.6 77.67 447.61 63.7 443.87 79.77 446.87 93.84 465.74 84.95 447.86 70.16 447.65 84.24 437.87 73.32 483.51 86.17 479.65 65.43 455.16 94.59 

Databricks visualization. Run in Databricks to view.

## Part 5: Data Preparation

The next step is to prepare the data for machine learning. Since all of this data is numeric and consistent this is a simple and straightforward task.

The goal is to use machine learning to determine a function that yields the output power as a function of a set of predictor features. The first step in building our ML pipeline is to convert the predictor features from DataFrame columns to Feature Vectors using the [pyspark.ml.feature.VectorAssembler()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.feature.VectorAssembler) method.

The VectorAssembler is a transformer that combines a given list of columns into a single vector column. It is useful for combining raw features and features generated by different feature transformers into a single feature vector, in order to train ML models like logistic regression and decision trees. VectorAssembler takes a list of input column names (each is a string) and the name of the output column (as a string).

### Exercise 5(a)

- Read the Spark documentation and useage examples for [VectorAssembler](https://spark.apache.org/docs/1.6.2/ml-features.html#vectorassembler)
- Convert the `power_plant` SQL table into a DataFrame named `dataset`
- Set the vectorizer's input columns to a list of the four columns of the input DataFrame: `["AT", "V", "AP", "RH"]`
- Set the vectorizer's output column name to `"features"`

In [0]:
# TODO: Uncomment the lines and replace <FILL_IN> with the appropriate code
from pyspark.ml.feature import VectorAssembler

datasetDF = sqlContext.table("power_plant")

vectorizer = VectorAssembler()
vectorizer.setInputCols(["AT", "V", "AP", "RH"])
vectorizer.setOutputCol("features")

VectorAssembler_acdc81401481

In [0]:
# TEST
assert_equal(set(vectorizer.getInputCols()), {"AT", "V", "AP", "RH"}, "Incorrect vectorizer input columns")
assert_equal(vectorizer.getOutputCol(), "features", "Incorrect vectorizer output column")

## Part 6: Data Modeling
Now let's model our data to predict what the power output will be given a set of sensor readings

Our first model will be based on simple linear regression since we saw some linear patterns in our data based on the scatter plots during the exploration stage.

We need a way of evaluating how well our linear regression model predicts power output as a function of input parameters. We can do this by splitting up our initial data set into a _Training Set_ used to train our model and a _Test Set_ used to evaluate the model's performance in giving predictions. We can use a DataFrame's [randomSplit()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrame.randomSplit) method to split our dataset. The method takes a list of weights and an optional random seed. The seed is used to initialize the random number generator used by the splitting function. 
However, in this part we just slice the dataframe by index and we will use randomSplit() in later parts.

### Exercise 6(a)

Use [monotonically_increasing_id()](https://spark.apache.org/docs/2.1.0/api/python/pyspark.sql.html#pyspark.sql.functions.monotonically_increasing_id) method to create index for `datasetDF` and divide up it into a trainingSetDF (80% of the input DataFrame) and a testSetDF (20% of the input DataFrame). Then cache each DataFrame in memory to maximize performance.

In [0]:

# TODO: Uncomment the following lines and replace <FILL_IN> with the appropriate code.
# # We'll hold out 20% of our data for testing and leave 80% for training
import pyspark.sql.functions as f
indexDF = datasetDF.withColumn('index', f.monotonically_increasing_id())
datasetSize = indexDF.count()
testSize = datasetSize * 0.2
trainSize = datasetSize * 0.8
# # take first 20% rows
split20DF = indexDF.sort('index').limit(int(testSize)).drop('index')
# # take last 80% rows
split80DF = indexDF.sort('index').limit(int(trainSize)).drop('index')

# # Let's cache these datasets for performance
testSetDF = split20DF.cache()
trainingSetDF = split80DF.cache()


In [0]:
# TEST
assert_equal(trainingSetDF.count(), 38272, "Incorrect size for training data set")
assert_equal(testSetDF.count(), 9568, "Incorrect size for test data set")

### Exercise 6(b)

Next we'll create a Linear Regression Model and use the built in help to identify how to train it. See API details for [Linear Regression](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.LinearRegression) in the ML guide.

- Read the documentation and examples for [Linear Regression](https://spark.apache.org/docs/1.6.2/ml-classification-regression.html#linear-regression)
- Run the next cell

In [0]:
# ***** LINEAR REGRESSION MODEL ****

from pyspark.ml.regression import LinearRegression
from pyspark.ml.regression import LinearRegressionModel
from pyspark.ml import Pipeline

# Let's initialize our linear regression learner
lr = LinearRegression()

# We use explain params to dump the parameters we can use
print(lr.explainParams())

aggregationDepth: suggested depth for treeAggregate (>= 2). (default: 2)
elasticNetParam: the ElasticNet mixing parameter, in range [0, 1]. For alpha = 0, the penalty is an L2 penalty. For alpha = 1, it is an L1 penalty. (default: 0.0)
epsilon: The shape parameter to control the amount of robustness. Must be > 1.0. Only valid when loss is huber (default: 1.35)
featuresCol: features column name. (default: features)
fitIntercept: whether to fit an intercept term. (default: True)
labelCol: label column name. (default: label)
loss: The loss function to be optimized. Supported options: squaredError, huber. (default: squaredError)
maxBlockSizeInMB: maximum memory in MB for stacking input data into blocks. Data is stacked within partitions. If more than remaining data size in a partition then it is adjusted to the data size. Default 0.0 represents choosing optimal value, depends on specific algorithm. Must be >= 0. (default: 0.0)
maxIter: max number of iterations (>= 0). (default: 100)
predic

### Exercise 6(c)
The cell below is based on the [Spark ML Pipeline API for Linear Regression](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.LinearRegression).

The first step is to set the parameters for the method:
- Set the name of the prediction column to "Predicted_PE"
- Set the name of the label column to "PE"
- Set the maximum number of iterations to 100
- Set the regularization parameter to 0.1

Next, we create the [ML Pipeline](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.Pipeline) and set the stages to the Vectorizer and Linear Regression learner we created earlier.

Finally, we create a model by training on `trainingSetDF`.

- Read the [Linear Regression](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.LinearRegression) documentation
- Run the next cell, and be sure you understand what's going on.

In [0]:
# Now we set the parameters for the method
lr.setPredictionCol("Predicted_PE")\
  .setLabelCol("PE")\
  .setMaxIter(100)\
  .setRegParam(0.1)


# We will use the new spark.ml pipeline API. If you have worked with scikit-learn this will be very familiar.
lrPipeline = Pipeline()

lrPipeline.setStages([vectorizer, lr])

# Let's first train on the entire dataset to see what we get
lrModel = lrPipeline.fit(trainingSetDF)

### Exercise 6(d)

From the Wikipedia article on [Linear Regression](https://en.wikipedia.org/wiki/Linear_regression):
> In statistics, linear regression is an approach for modeling the relationship between a scalar dependent variable \\( y \\) and one or more explanatory variables (or independent variables) denoted \\(X\\). In linear regression, the relationships are modeled using linear predictor functions whose unknown model parameters are estimated from the data. Such models are called linear models.

Linear regression has many practical uses. Most applications fall into one of the following two broad categories:
  - If the goal is prediction, or forecasting, or error reduction, linear regression can be used to fit a predictive model to an observed data set of \\(y\\) and \\(X\\) values. After developing such a model, if an additional value of \\(X\\) is then given without its accompanying value of \\(y\\), the fitted model can be used to make a prediction of the value of \\(y\\).
  - Given a variable \\(y\\) and a number of variables \\( X_1 \\), ..., \\( X_p \\) that may be related to \\(y\\), linear regression analysis can be applied to quantify the strength of the relationship between \\(y\\) and the \\( X_j\\), to assess which \\( X_j \\) may have no relationship with \\(y\\) at all, and to identify which subsets of the \\( X_j \\) contain redundant information about \\(y\\).

We are interested in both uses, as we would like to predict power output as a function of the input variables, and we would like to know which input variables are weakly or strongly correlated with power output.

Since Linear Regression is simply a Line of best fit over the data that minimizes the square of the error, given multiple input dimensions we can express each predictor as a line function of the form:

\\[ y = a + b x_1 + b x_2 + b x_i ... \\]

where \\(a\\) is the intercept and the \\(b\\) are the coefficients.

To express the coefficients of that line we can retrieve the Estimator stage from the PipelineModel and express the weights and the intercept for the function.

Run the next cell. Ensure that you understand what's going on.

In [0]:
# The intercept is as follows:
intercept = lrModel.stages[1].intercept

# The coefficents (i.e., weights) are as follows:
weights = lrModel.stages[1].coefficients

# Create a list of the column names (without PE)
featuresNoLabel = [col for col in datasetDF.columns if col != "PE"]

# Merge the weights and labels
# Sort the coefficients from greatest absolute weight most to the least absolute weight
coefficents = sorted(zip(weights, featuresNoLabel), key=lambda tup: abs(tup[0]), reverse=True)

equation = "y = {intercept}".format(intercept=intercept)
variables = []
for x in coefficents:
    weight = abs(x[0])
    name = x[1]
    symbol = "+" if (x[0] > 0) else "-"
    equation += (" {} ({} * {})".format(symbol, weight, name))

# Finally here is our equation
print("Linear Regression Equation: " + equation)

Linear Regression Equation: y = 437.18102707794225 - (1.9176785983589777 * AT) - (0.2549116118186099 * V) - (0.14699064760932545 * RH) + (0.07844750035393125 * AP)


### Exercise 6(e)

Recall **Part 4: Visualize Your Data** when we visualized each predictor against Power Output using a Scatter Plot, does the final equation seems logical given those visualizations?

Now let's see what our predictions look like given this model. We apply our Linear Regression model to the 20% of the data that we split from the input dataset. The output of the model will be a predicted Power Output column named "Predicted_PE".

- Run the next cell
- Scroll through the resulting table and notice how the values in the Power Output (PE) column compare to the corresponding values in the predicted Power Output (Predicted_PE) column

In [0]:
# Apply our LR model to the test data and predict power output
predictionsAndLabelsDF = lrModel.transform(testSetDF).select("AT", "V", "AP", "RH", "PE", "Predicted_PE")

display(predictionsAndLabelsDF)

AT V AP RH PE Predicted_PE 14.96 41.76 1024.07 73.17 463.26 467.4278723388228 25.18 62.96 1020.04 59.08 444.37 444.18002569142857 5.11 39.4 1012.16 92.14 488.56 483.19587562218646 20.86 57.32 1010.24 76.64 446.48 450.55215745150804 10.82 37.5 1009.23 96.62 473.9 471.84189361068525 26.27 59.44 1012.23 58.77 443.67 442.4199370158135 15.89 43.96 1014.02 75.24 467.35 463.99095767723975 9.48 44.71 1019.12 66.43 478.42 477.7871636411 14.64 45.0 1021.78 41.25 475.98 471.72791256388456 11.74 43.56 1015.14 70.72 477.5 472.80354743274745 17.99 43.72 1008.64 75.04 453.02 459.63236198514005 20.14 46.93 1014.66 64.22 453.99 456.7537794839941 24.34 73.5 1011.31 84.15 440.29 438.7342051118264 25.71 58.59 1012.77 61.83 451.28 443.30308216944695 26.19 69.34 1009.48 87.59 433.99 435.5977252566039 21.42 43.79 1015.76 43.08 462.19 458.29324788005545 18.21 45.0 1022.86 48.84 467.54 463.85086425277046 11.04 41.74 1022.6 77.51 477.2 474.1970134404816 14.45 52.75 1023.97 63.59 459.85 467.00473546416134 13.97 38.47 1015.15 55.28 464.3 472.0949443366552 17.76 42.42 1009.09 66.26 468.27 461.73069241929596 5.41 40.07 1019.16 64.77 495.24 487.022047790305 7.76 42.28 1008.52 83.31 483.8 478.3922604115996 27.23 63.9 1014.3 47.19 443.61 441.3065977977265 27.36 48.6 1003.18 54.93 436.06 442.94740342433266 27.47 70.72 1009.97 74.62 443.25 434.7362266010611 14.6 39.31 1011.11 72.52 464.16 467.8216343995468 7.91 39.96 1023.57 88.44 475.52 479.12257641935577 5.81 35.79 1012.14 92.28 484.41 482.751583881328 30.53 65.18 1012.69 41.85 437.89 435.310601142678 23.87 63.94 1019.02 44.28 445.11 448.5378164099536 26.09 58.41 1013.64 64.58 438.86 442.2842734365801 29.27 66.85 1011.11 63.25 440.98 434.0316268754745 27.38 74.16 1010.08 78.61 436.65 433.45405827133516 24.81 63.94 1018.76 44.51 444.26 446.680994328454 12.75 44.03 1007.29 89.46 465.86 467.376465976873 24.66 63.73 1011.4 74.52 444.37 442.033614619329 16.38 47.45 1010.08 88.86 450.69 459.85055786696336 13.91 39.35 1014.69 75.51 469.02 468.9759761828569 23.18 51.3 1012.04 78.64 448.86 447.4849352118817 22.47 47.45 1007.62 76.65 447.14 449.7736701593964 13.39 44.85 1017.24 80.44 469.18 468.0465324221898 9.28 41.54 1018.33 79.89 482.8 476.9383015281357 11.82 42.86 1014.12 88.28 476.7 470.167399050771 10.27 40.64 1020.63 84.6 474.99 474.7573234669712 22.92 63.94 1019.28 42.69 444.22 450.6137225581855 16.0 37.87 1020.24 78.41 461.33 465.3544078466755 21.22 43.43 1010.96 61.07 448.06 455.74764202779136 13.46 44.71 1014.51 50.0 474.6 472.2082161832209 9.39 40.11 1029.14 77.29 473.05 478.3220736498271 31.07 73.5 1010.58 43.66 432.06 431.7226127913137 12.82 38.62 1018.71 83.8 467.41 470.34913781443726 32.57 78.92 1011.6 66.47 430.12 424.19163373611065 8.11 42.18 1014.82 93.09 473.62 476.8032147819664 13.92 39.39 1012.94 80.52 471.81 468.0728966622585 23.04 59.43 1010.23 68.99 442.99 446.957448585356 27.31 64.44 1014.65 57.27 442.77 439.56132213669764 5.91 39.33 1010.18 95.53 491.49 481.0259522102302 25.26 61.08 1013.68 71.72 447.46 442.148957345746 27.97 58.84 1002.25 57.88 446.11 438.6607459885345 26.08 52.3 1007.03 63.34 442.44 443.52469059647154 29.01 65.71 1013.61 48.07 446.22 437.24825933011545 12.18 40.1 1016.67 91.87 471.49 469.8529355049662 13.76 45.87 1008.89 87.27 463.5 465.41799874561497 25.5 58.79 1016.02 64.4 440.01 443.5320007645329 28.26 65.34 1014.56 43.4 441.03 439.5418070249293 21.39 62.96 1019.49 72.24 452.68 449.47048453147573 7.26 40.69 1020.43 90.22 474.91 479.67501352780556 10.54 34.03 1018.71 74.0 478.77 477.3319976635146 27.71 74.34 998.14 71.85 434.2 432.8323338673624 23.11 68.3 1017.83 86.62 437.91 442.5669009719773 7.51 41.01 1024.61 97.41 477.61 478.38506995760224 26.46 74.67 1016.65 84.44 431.65 434.7467622615609 29.34 74.34 998.58 81.55 430.57 428.31522537038256 10.32 42.28 1008.82 75.66 481.09 474.63101590411816 22.74 61.02 1009.56 79.41 445.56 445.5432403287458 13.48 39.85 1012.71 58.91 475.74 471.95784087385596 25.52 69.75 1010.36 90.06 435.12 436.4840230573752 21.58 67.25 1017.39 79.0 4

### Exercise 6(f)

From a visual inspection of the predictions, we can see that they are close to the actual values.

However, we would like a scientific measure of how well the Linear Regression model is performing in accurately predicting values. To perform this measurement, we can use an evaluation metric such as [Root Mean Squared Error](https://en.wikipedia.org/wiki/Root-mean-square_deviation) (RMSE) to validate our Linear Regression model.

RSME is defined as follows: \\( RMSE = \sqrt{\frac{\sum_{i = 1}^{n} (x_i - y_i)^2}{n}}\\) where \\(y_i\\) is the observed value and \\(x_i\\) is the predicted value

RMSE is a frequently used measure of the differences between values predicted by a model or an estimator and the values actually observed. The lower the RMSE, the better our model.

Spark ML Pipeline provides several regression analysis metrics, including [RegressionEvaluator()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.RegressionEvaluator).

After we create an instance of [RegressionEvaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.RegressionEvaluator), we set the label column name to "PE" and set the prediction column name to "Predicted_PE". We then invoke the evaluator on the predictions.

Run the next cell and ensure that you understand what's going on.

In [0]:
# Now let's compute an evaluation metric for our test dataset
from pyspark.ml.evaluation import RegressionEvaluator

# Create an RMSE evaluator using the label and predicted columns
regEval = RegressionEvaluator(predictionCol="Predicted_PE", labelCol="PE", metricName="rmse")

# Run the evaluator on the DataFrame
rmse = regEval.evaluate(predictionsAndLabelsDF)

print("Root Mean Squared Error: %.2f" % rmse)

Root Mean Squared Error: 4.56


### Exercise 6(g)

Another useful statistical evaluation metric is the coefficient of determination, denoted \\(R^2\\) or \\(r^2\\) and pronounced "R squared". It is a number that indicates the proportion of the variance in the dependent variable that is predictable from the independent variable and it provides a measure of how well observed outcomes are replicated by the model, based on the proportion of total variation of outcomes explained by the model. The coefficient of determination ranges from 0 to 1 (closer to 1), and the higher the value, the better our model.

To compute \\(r^2\\), we invoke the evaluator with  `regEval.metricName: "r2"`

Run the next cell and ensure that you understand what's going on.

In [0]:
# Now let's compute another evaluation metric for our test dataset
r2 = regEval.evaluate(predictionsAndLabelsDF, {regEval.metricName: "r2"})

print("r2: {0:.2f}".format(r2))

r2: 0.93


### Exercise 6(h)

Generally, assuming a Gaussian distribution of errors, a good model will have 68% of predictions within 1 RMSE and 95% within 2 RMSE of the actual value (see http://statweb.stanford.edu/~susan/courses/s60/split/node60.html).

Let's examine the predictions and see if the RMSE meets this criteria.

We create a new DataFrame using [selectExpr()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.sql.html#pyspark.sql.DataFrame.selectExpr) to project a set of SQL expressions, and register the DataFrame as a SQL table using createOrReplaceTempView().

Run the next cell and ensure that you understand what's going on.

In [0]:
# First we remove the table if it already exists
sqlContext.sql("DROP TABLE IF EXISTS Power_Plant_RMSE_Evaluation")
# dbutils.fs.rm("dbfs:/user/hive/warehouse/Power_Plant_RMSE_Evaluation", True)

# Next we calculate the residual error and divide it by the RMSE
predictionsAndLabelsDF.selectExpr("PE", "Predicted_PE", "PE - Predicted_PE Residual_Error", "(PE - Predicted_PE) / {} Within_RSME".format(rmse)).createOrReplaceTempView("Power_Plant_RMSE_Evaluation")

### Exercise 6(i)

We can use SQL to explore the `Power_Plant_RMSE_Evaluation` table. First let's look at at the table using a SQL SELECT statement.

Run the next cell and ensure that you understand what's going on.

In [0]:
#%sql SELECT * from Power_Plant_RMSE_Evaluation

# Comment out this cell before uploading to Gradescope

### Exercise 6(j)

Now we can display the RMSE as a Histogram.

Perform the following steps:

- Run the following cell
- Click on the drop down next to the "Bar chart" icon a select "Histogram" to turn the table into a Histogram plot

<img src="http://spark-mooc.github.io/web-assets/images/cs110x/change-plot-type-histogram.png" style="border: 1px solid #999999"/>


- Click on "Plot Options..."
- In the "All Fields:" box, click on "&lt;id&gt;" and drag it into the "Keys:" box
- Change the "Aggregation" to "COUNT"

<img src="http://spark-mooc.github.io/web-assets/images/cs110x/customize-plot-histogram.png" style="border: 1px solid #999999"/>

- Apply your changes by clicking the Apply button
- Increase the size of the graph by clicking and dragging the size control

Notice that the histogram clearly shows that the RMSE is centered around 0 with the vast majority of the error within 2 RMSEs.

In [0]:
# %sql -- Now we can display the RMSE as a Histogram
# SELECT Within_RSME  from Power_Plant_RMSE_Evaluation

# Comment out this cell before uploading to Gradescope

### Exercise 6(k)

Using a complex SQL SELECT statement, we can count the number of predictions within + or - 1.0 and + or - 2.0 and then display the results as a pie chart.

Perform the following steps:

  - Run the following cell
  - Click on the drop down next to the "Bar chart" icon a select "Pie" to turn the table into a Pie Chart plot
  - Increase the size of the graph by clicking and dragging the size control

In [0]:
# %sql SELECT case when Within_RSME <= 1.0 AND Within_RSME >= -1.0 then 1
#             when  Within_RSME <= 2.0 AND Within_RSME >= -2.0 then 2 else 3
#        end RSME_Multiple, COUNT(*) AS count
# FROM Power_Plant_RMSE_Evaluation
# GROUP BY case when Within_RSME <= 1.0 AND Within_RSME >= -1.0 then 1  when  Within_RSME <= 2.0 AND Within_RSME >= -2.0 then 2 else 3 end

# Comment out this cell before uploading to Gradescope

From the pie chart, we can see that 68% of our test data predictions are within 1 RMSE of the actual values, and 97% (68% + 29%) of our test data predictions are within 2 RMSE. So the model is pretty decent. Let's see if we can tune the model to improve it further.

## Part 7: Tuning and Evaluation

Now that we have a model with all of the data let's try to make a better model by tuning over several parameters. The process of tuning a model is known as [Model Selection](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#module-pyspark.ml.tuning) or [Hyperparameter Tuning](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#module-pyspark.ml.tuning), and Spark ML Pipeline makes the tuning process very simple and easy.

An important task in ML is model selection, or using data to find the best model or parameters for a given task. This is also called tuning. Tuning may be done for individual Estimators such as [LinearRegression](https://spark.apache.org/docs/1.6.2/ml-classification-regression.html#linear-regression), or for entire Pipelines which include multiple algorithms, featurization, and other steps. Users can tune an entire Pipeline at once, rather than tuning each element in the Pipeline separately.

Spark ML Pipeline supports model selection using tools such as [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator), which requires the following items:
  - [Estimator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.Estimator): algorithm or Pipeline to tune
  - [Set of ParamMaps](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.ParamGridBuilder): parameters to choose from, sometimes called a _parameter grid_ to search over
  - [Evaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.Evaluator): metric to measure how well a fitted Model does on held-out test data

At a high level, model selection tools such as [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) work as follows:
  - They split the input data into separate training and test datasets.
  - For each (training, test) pair, they iterate through the set of ParamMaps:
    - For each [ParamMap](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.ParamGridBuilder), they fit the [Estimator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.Estimator) using those parameters, get the fitted Model, and evaluate the Model's performance using the [Evaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.Evaluator).
  - They select the Model produced by the best-performing set of parameters.

The [Evaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.Evaluator) can be a [RegressionEvaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.RegressionEvaluator) for regression problems. To help construct the parameter grid, users can use the [ParamGridBuilder](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.ParamGridBuilder) utility.

Note that cross-validation over a grid of parameters is expensive. For example, in the next cell, the parameter grid has 10 values for [lr.regParam](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.LinearRegression.regParam), and [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) uses 3 folds. This multiplies out to (10 x 3) = 30 different models being trained. In realistic settings, it can be common to try many more parameters (e.g., multiple values for multiple parameters) and use more folds (_k_ = 3 and _k_ = 10 are common). In other words, using [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) can be very expensive. However, it is also a well-established method for choosing parameters which is more statistically sound than heuristic hand-tuning.

We perform the following steps:
  - Create a [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) using the Pipeline and [RegressionEvaluator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.evaluation.RegressionEvaluator) that we created earlier, and set the number of folds to 3
  - Create a list of 10 regularization parameters
  - Use [ParamGridBuilder](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.ParamGridBuilder) to build a parameter grid with the regularization parameters and add the grid to the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator)
  - Run the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) to find the parameters that yield the best model (i.e., lowest RMSE) and return the best model.

### Exercise 7(a)

Run the next cell. _Note that it will take some time to run the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) as it will run almost 200 Spark jobs_

In [0]:
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

# We can reuse the RegressionEvaluator, regEval, to judge the model based on the best Root Mean Squared Error
# Let's create our CrossValidator with 3 fold cross validation
crossval = CrossValidator(estimator=lrPipeline, evaluator=regEval, numFolds=3)

# Let's tune over our regularization parameter from 0.01 to 0.10
regParam = [x / 100.0 for x in range(1, 11)]

# We'll create a paramter grid using the ParamGridBuilder, and add the grid to the CrossValidator
paramGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, regParam)
             .build())
crossval.setEstimatorParamMaps(paramGrid)

# Now let's find and return the best model
cvModel = crossval.fit(trainingSetDF).bestModel

### Exercise 7(b)

Now that we have tuned our Linear Regression model, let's see what the new RMSE and \\(r^2\\) values are versus our intial model.

Complete and run the next cell.

In [0]:
# TODO: Uncomment the following lines and replace <FILL_IN> with the appropriate code.

# # Now let's use cvModel to compute an evaluation metric for our test dataset: testSetDF
predictionsAndLabelsDF = cvModel.transform(testSetDF)

# # Run the previously created RMSE evaluator, regEval, on the predictionsAndLabelsDF DataFrame
rmseNew = regEval.evaluate(predictionsAndLabelsDF)

# # Now let's compute the r2 evaluation metric for our test dataset
regEval.setMetricName("r2")
r2New = regEval.evaluate(predictionsAndLabelsDF)


print("Original Root Mean Squared Error: {0:2.2f}".format(rmse))
print("New Root Mean Squared Error: {0:2.2f}".format(rmseNew))
print("Old r2: {0:2.2f}".format(r2))
print("New r2: {0:2.2f}".format(r2New))


Original Root Mean Squared Error: 4.56
New Root Mean Squared Error: 4.56
Old r2: 0.93
New r2: 0.93


In [0]:
# TEST
assert_equal(round(rmse, 2), 4.56, "Incorrect value for rmse")
assert_equal(round(rmseNew, 2), 4.56, "Incorrect value for rmseNew")
assert_equal(round(r2, 2), 0.93, "Incorrect value for r2")
assert_equal(round(r2New, 2), 0.93, "Incorrect value for r2New")

So our initial untuned and tuned linear regression models are identical. Let's look at the regularization parameter that the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) has selected.

Recall that the orginal regularization parameter we used was 0.01.

**NOTE**: The ML Python API currently doesn't provide a way to query the regularization parameter, so we cheat, by "reaching through" to the JVM version of the API.

In [0]:
print("Regularization parameter of the best model: {0:.2f}".format(cvModel.stages[-1]._java_obj.parent().getRegParam()))

Regularization parameter of the best model: 0.01


### Exercise 7(c)

Maybe we can try an [Ensemble Learning](https://en.wikipedia.org/wiki/Ensemble_learning) method. [Random forests](https://en.wikipedia.org/wiki/Random_forest) or random decision tree forests are an ensemble learning method for regression that operate by constructing a multitude of decision trees at training time and outputting the class that is the mean prediction (regression) of the individual trees. Random decision forests correct for decision trees' habit of overfitting to their training set.

Spark ML Pipeline provides [RandomForestRegressor()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.RandomForestRegressor) as an implementation of [Random forests](https://en.wikipedia.org/wiki/Random_forest).

The cell below is based on the [Spark ML Pipeline API for Random Forest Regressor](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.RandomForestRegressor).

- Read the [Random Forest Regressor](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.RandomForestRegressor) documentation
- In the next cell, create a [RandomForestRegressor()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.RandomForestRegressor)
- The next step is to set the parameters for the method (we do this for you):
  - Set the name of the prediction column to "Predicted_PE"
  - Set the name of the features column to "features"
  - Set the random number generator seed to 100088121L
  - Set the maximum depth to 8
  - Set the number of trees to 30
- Create the [ML Pipeline](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.Pipeline) and set the stages to the Vectorizer we created earlier and [RandomForestRegressor()](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.regression.RandomForestRegressor) learner we just created.

In [0]:
# TODO: Uncomment the following lines and replace <FILL_IN> with the appropriate code.

from pyspark.ml.regression import RandomForestRegressor

# # Create a RandomForestRegressor
rf = RandomForestRegressor()

rf.setLabelCol("PE")\
  .setPredictionCol("Predicted_PE")\
  .setFeaturesCol("features")\
  .setSeed(100088121)\
  .setMaxDepth(8)\
  .setNumTrees(30)

# # Create a Pipeline
rfPipeline = Pipeline()

# # Set the stages of the Pipeline
rfPipeline.setStages([vectorizer, rf])


Pipeline_8d7625edf81d

In [0]:
# TEST

assert_equal(rfPipeline.getStages()[0].__class__.__name__, 'VectorAssembler', "Stage 0 of pipeline is not correct")
assert_equal(rfPipeline.getStages()[1].__class__.__name__, 'RandomForestRegressor', "Stage 1 of pipeline is not correct")

### Exercise 7(d)

Instead guessing what parameters to use, we will use [Model Selection](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#module-pyspark.ml.tuning) or [Hyperparameter Tuning](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#module-pyspark.ml.tuning) to create the best model.

We can reuse the existing [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) by replacing the Estimator with our new `rfPipeline` (the number of folds remains 3).

- Use [ParamGridBuilder](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.ParamGridBuilder) to build a parameter grid with the parameter `rf.maxBins` and a list of the values 50 and 100, and add the grid to the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator)
- Run the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) to find the parameters that yield the best model (i.e., lowest RMSE) and return the best model.

_Note that it will take some time to run the [CrossValidator](https://spark.apache.org/docs/1.6.2/api/python/pyspark.ml.html#pyspark.ml.tuning.CrossValidator) as it will run almost 100 Spark jobs, and each job takes longer to run than the prior CrossValidator runs._

In [0]:
# TODO: Uncomment the following lines and replace <FILL_IN> with the appropriate code.
# # Let's just reuse our CrossValidator with the new rfPipeline,  RegressionEvaluator regEval, and 3 fold cross validation
crossval.setEstimator(rfPipeline)

# # Let's tune over our rf.maxBins parameter on the values 50 and 100, create a parameter grid using the ParamGridBuilder
paramGrid = (ParamGridBuilder()
             .addGrid(rf.maxBins, [50, 100])
             .build())

# # Add the grid to the CrossValidator
crossval.setEstimatorParamMaps(paramGrid)

# # Now let's find and return the best model
rfModel = crossval.fit(trainingSetDF).bestModel


In [0]:
# TEST
assert_equal(rfModel.stages[0].__class__.__name__, 'VectorAssembler', 'rfModel has incorrect stage 0')
assert_equal(rfModel.stages[1].__class__.__name__, 'RandomForestRegressionModel', 'rfModel has incorrect stage 1')

### Exercise 7(e)

Now let's see how our tuned RandomForestRegressor model's RMSE and \\(r^2\\) values compare to our tuned LinearRegression model.

Complete and run the next cell.

In [0]:
# TODO: Uncomment the following lines and replace <FILL_IN> with the appropriate code.

# # Now let's use rfModel to compute an evaluation metric for our test dataset: testSetDF
predictionsAndLabelsDF = rfModel.transform(testSetDF)

# # Run the previously created RMSE evaluator, regEval, on the predictionsAndLabelsDF DataFrame
rmseRF = regEval.evaluate(predictionsAndLabelsDF, {regEval.metricName: "rmse"})

# # Now let's compute the r2 evaluation metric for our test dataset
r2RF = regEval.evaluate(predictionsAndLabelsDF, {regEval.metricName: "r2"})


print("LR Root Mean Squared Error: {0:.2f}".format(rmseNew))
print("RF Root Mean Squared Error: {0:.2f}".format(rmseRF))
print("LR r2: {0:.2f}".format(r2New))
print("RF r2: {0:.2f}".format(r2RF))

LR Root Mean Squared Error: 4.56
RF Root Mean Squared Error: 3.39
LR r2: 0.93
RF r2: 0.96


In [0]:
# TEST
assert_true(abs(round(rmseRF, 2) - 3.35) < 0.05, "Incorrect value for rmseRF")
# assert_equal(round(rmseRF, 2), 3.4, "Incorrect value for rmseRF")
assert_equal(round(r2RF, 2), 0.96, "Incorrect value for r2RF")

Note that the `r2` values are similar for all three. However, the RMSE for the Random Forest model is better.

The line below will pull the Random Forest model from the Pipeline and display it as an if-then-else string.

**ToDo**: Run the next cell

In [0]:
print (rfModel.stages[-1]._java_obj.toDebugString())

RandomForestRegressionModel: uid=RandomForestRegressor_5d82a6c65021, numTrees=30, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 2 <= 1015.005)
     If (feature 1 <= 46.345)
      If (feature 3 <= 77.245)
       If (feature 0 <= 14.855)
        If (feature 0 <= 9.254999999999999)
         If (feature 3 <= 74.735)
          If (feature 2 <= 1005.38)
           If (feature 2 <= 1004.995)
            Predict: 484.3654545454546
           Else (feature 2 > 1004.995)
            Predict: 485.16842105263163
          Else (feature 2 > 1005.38)
           If (feature 0 <= 7.355)
            Predict: 492.8498148148148
           Else (feature 0 > 7.355)
            Predict: 484.59658536585346
         Else (feature 3 > 74.735)
          If (feature 1 <= 37.84)
           If (feature 1 <= 36.85)
            Predict: 480.62999999999994
           Else (feature 1 > 36.85)
            Predict: 480.11666666666656
          Else (feature 1 > 37.84)
           If (feature 0 <= 6.175)
          

### Conclusion

Wow! So our best model is in fact our Random Forest tree model which uses an ensemble of 30 Trees that consider 4 features at each split. Think about if this "best" model is good. How might we want to use it in the business problem?